In [1]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-

import platform as plat
import os
import time

import keras as kr
import numpy as np
import random
import pdb

import tensorflow as tf
from keras.models import Sequential, Model
from keras.layers import Dense, Dropout, Input, Reshape, BatchNormalization # , Flatten
from keras.layers import Lambda, TimeDistributed, Activation,Conv2D, MaxPooling2D,GRU, Bidirectional #, Merge
from keras.layers.merge import add, concatenate
from keras import backend as K
from keras.optimizers import SGD, Adadelta, Adam

# 指定第一块GPU可用
os.environ["CUDA_VISIBLE_DEVICES"] = "0"
config = tf.ConfigProto()
config.gpu_options.allow_growth=True   #不全部占满显存, 按需分配
# config.gpu_options.per_process_gpu_memory_fraction = 0.3
sess = tf.Session(config=config)
K.set_session(sess)

Using TensorFlow backend.


In [2]:
from utils.common import *
from utils.wav_preprocess import compute_freq_feature
from speech_data import test_data_generator

py2id_dict = pinyin2id()
id2py_dict = dict(zip(py2id_dict.values(), py2id_dict.keys()))

## 搭建模型

In [3]:
MODEL_LOGS_DIR_NAME = "logs_speechRec_1"

class SpeechRecognitionModelV1():
    '''
    定义CNN/LSTM/CTC模型，使用函数式模型
    输入层：200维的特征值序列，一条语音数据的最大长度设为1600（大约16s）
    隐藏层：卷积池化层，卷积核大小为3x3，池化窗口大小为2
    隐藏层：全连接层
    输出层：全连接层，神经元数量为self.MS_OUTPUT_SIZE，使用softmax作为激活函数，
    CTC层：使用CTC的loss作为损失函数，实现连接性时序多输出

    '''

    def __init__(self):
        '''
        初始化
        默认输出的拼音的表示大小是1423，即1423个拼音+1个空白块
        '''
        self.MS_OUTPUT_SIZE = 1422 + 1 + 1  # 神经网络最终输出的每一个字符向量维度的大小
        # self.BATCH_SIZE = BATCH_SIZE # 一次训练的batch
        self.label_max_string_length = 64
        self.AUDIO_LENGTH = 16000
        self.AUDIO_FEATURE_LENGTH = 200

        self.model, self.ctc_model = self._model_init()

    def _model_init(self):
        input_data = Input(name="the_inputs", shape=(None, self.AUDIO_FEATURE_LENGTH, 1))

        x = Conv2D(32, (3, 3), use_bias=False, activation='relu', padding='same', kernel_initializer='he_normal')(
            input_data)
        x = BatchNormalization()(x)
        x = Conv2D(32, (3, 3), use_bias=True, activation='relu', padding='same', kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)
        x = MaxPooling2D(pool_size=2, strides=None, padding='valid')(x)

        x = Conv2D(64, (3, 3), use_bias=True, activation='relu', padding='same', kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)
        x = Conv2D(64, (3, 3), use_bias=True, activation='relu', padding='same', kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)

        x = Conv2D(64, (3, 3), use_bias=True, activation='relu', padding='same', kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)
        x = Conv2D(64, (3, 3), use_bias=True, activation='relu', padding='same', kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)
        x = MaxPooling2D(pool_size=2, strides=None, padding='valid')(x)

        x = Conv2D(128, (3, 3), use_bias=True, activation='relu', padding='same', kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)
        x = Conv2D(128, (3, 3), use_bias=True, activation='relu', padding='same', kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)

        x = Conv2D(128, (3, 3), use_bias=True, activation='relu', padding='same', kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)
        x = Conv2D(128, (3, 3), use_bias=True, activation='relu', padding='same', kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)

        x = Conv2D(128, (3, 3), use_bias=True, activation='relu', padding='same', kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)
        x = Conv2D(128, (3, 3), use_bias=True, activation='relu', padding='same', kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)
        x = MaxPooling2D(pool_size=2, strides=None, padding='valid')(x)

        # 200 / 8 * 128 = 3200
        # 因为DFT抽样点数必须为2的整数次幂，经过3层maxpooling层，要求音频数据的每个维度需要能够被8整除
        x = Reshape(target_shape=(-1, 3200))(x)

        # x = Dropout(0.2)(x)
        x = Dense(128, activation='relu', use_bias=True, kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)

        gru_units = 128
        # 创建一个双向GRU，看看是否能增加精度？
        #         gru_1a = GRU(gru_units, return_sequences=True, kernel_initializer='he_normal', name='gru_1a')(x)
        #         gru_1b = GRU(gru_units, return_sequences=True, go_backwards=True, kernel_initializer='he_normal', name='gru_1b')(x)
        x = Bidirectional(GRU(gru_units, return_sequences=True, kernel_initializer='he_normal', name='gru_1'))(x)
        x = BatchNormalization()(x)

        x = Bidirectional(GRU(gru_units, return_sequences=True, kernel_initializer='he_normal', name='gru_2'))(x)
        x = BatchNormalization()(x)

        x = Dense(128, activation='relu', use_bias=True, kernel_initializer='he_normal')(x)
        x = BatchNormalization()(x)

        x = Dense(self.MS_OUTPUT_SIZE, use_bias=True, kernel_initializer='he_normal')(x)

        y_pred = Activation('softmax', name='y_pred_activation')(x)
        model_data = Model(inputs=input_data, outputs=y_pred)

        labels = Input(name='the_labels', shape=[None], dtype='float32')
        input_length = Input(name='input_length', shape=[1], dtype='int64')
        label_length = Input(name='label_length', shape=[1], dtype='int64')
        loss_out = Lambda(self._ctc_batch_cost_func, output_shape=(1,), name='ctc_loss')(
            [y_pred, labels, input_length, label_length])

        ctc_model = Model(inputs=[input_data, labels, input_length, label_length], outputs=loss_out)
        ctc_model.summary()

        optimizer = Adam(learning_rate=0.0003, beta_1=0.9, beta_2=0.999, decay=0.0, epsilon=10e-8)
        ctc_model.compile(optimizer=optimizer, loss={'ctc_loss': lambda y_true, y_pred: y_pred}, metrics=['acc'])

        # captures output of softmax so we can decode the output during visualization
        #         test_func = K.function([input_data], [self.y_pred])
        #         pdb.set_trace()

        # print('[*提示] 创建模型成功，模型编译成功')
        print('[*Info] Create Model Successful, Compiles Model Successful. ')
        return model_data, ctc_model

    def _ctc_batch_cost_func(self, args):
        y_pred, labels, input_length, label_length = args

        #         pdb.set_trace()
        y_pred = y_pred[:, :, :]
        return K.ctc_batch_cost(labels, y_pred, input_length, label_length)

    def predict(self, data_input, input_len):
        '''
        预测结果，返回拼音对应的id列表
        :param data_input: 输入的音频数据
        :param input_len: 音频的长度
        :return:
        '''
        batch_size = 1

        base_pred = self.model.predict(data_input, batch_size)
#         print("base_pred-pre:", base_pred)
        base_pred = base_pred[:, :, :]
#         print("base_pred:", base_pred)

        r = K.ctc_decode(base_pred, input_len, greedy=True, beam_width=100, top_paths=1)
#         print("r:", r)
        r1 = K.get_value(r[0][0])
#         print("r1:", r1)

        return r1

    def recognize(self, wav_file):
        '''
        wav 文件识别出拼音
        :param wav_file:
        :return:
        '''
        data_input = compute_freq_feature(wav_file)
        input_length = len(data_input) // 8

        data_input = np.array(data_input, dtype=np.float)
        data_input = np.reshape(data_input.shape[0], data_input.shape[1], 1)

        r1 = self.predict(data_input, input_length)
        recognize_pingyin_list = [id2py_dict[id] for id in r1]
        return recognize_pingyin_list

    def test_model(self, wav_label_list, data_batch_size=4):
        '''
        验证模型的水准
        :param wav_data_path:  验证集wav数据集合
        :param labels_data_path: 对应的拼音labels id集合
        :param data_batch_size: 验证集的数量
        :return:
        '''

        for next_index in range(data_batch_size):
            batch = data_generator(wav_label_list, 1)

            word_error_num = 0
            word_total_num = 0
            input, output = next(batch)

            y_predict = self.predict(input, input['input_length'])
            label = input['the_labels']

            real_str = ''.join([id2py_dict[id] for id in label[0].tolist()])
            predict_str = ''.join([id2py_dict[id] for id in y_predict[0].tolist()])

            words_num = label.shape[1]
            word_total_num += words_num
            distance = calculate_sequence_edit_distance(label[0].tolist(), y_predict[0].tolist())
            if distance <= words_num:
                word_error_num += distance  # 使用编辑距离作为错误字数
            else:  # 否则肯定是增加了一堆乱七八糟的奇奇怪怪的字,就直接加句子本来的总字数就好了
                word_error_num += words_num

            print("[原本语音内容]：", real_str)
            print('[**预测结果**]：', predict_str)
            print("============********============" + "\n")

        acc = (word_total_num - word_error_num) / word_total_num
        print('*本轮语音测试准确率：', str(acc))

    def load_last_weights(self):
        sorted_model_list = sorted(glob.glob(os.path.join(MODEL_LOGS_DIR_NAME, '*.model')),
                                   key=lambda x: time.localtime(os.path.getmtime(x)),
                                   reverse=True)
        if len(sorted_model_list) == 0:
            return
        sorted_ctc_model_list = sorted(glob.glob(os.path.join(MODEL_LOGS_DIR_NAME, '*.model.base')),
                                       key=lambda x: time.localtime(os.path.getmtime(x)),
                                       reverse=True)

        self.model.load_weights(sorted_model_list[0])
        self.ctc_model.load_weights(sorted_ctc_model_list[0])

## 训练模型

In [4]:
from utils.wav_preprocess import *

train_wav_list = load_various_wav_train_data()[:80000]
validation_wav_list = load_various_wav_dev_data()

load_various_wav_train_data start, please wait...


421it [05:43,  1.23it/s]


load_various_wav_train_data has ended...


61it [00:50,  1.20it/s]


In [ ]:
from speech_data import *
# from speechRecognitionModelV1 import SpeechRecognitionModelV1

m = SpeechRecognitionModelV1()

epochs = 100
batch_size = 4

batch_num = len(train_wav_list) // batch_size
# val_batch_num = int(batch_num * 0.2)

train_batch = data_generator(train_wav_list, batch_size)
# validation_batch = data_generator(validation_wav_list, batch_size)

m.load_last_weights()

for i in range(epochs):
    print("Begin epoch:", i+1)
    train_batch = data_generator(train_wav_list, batch_size)
    history = m.ctc_model.fit_generator(train_batch,
                                        steps_per_epoch=batch_num,
                                        epochs=1)
    m.test_model(wav_label_list=validation_wav_list, data_batch_size=32)

    m.model.save_weights(os.path.join(MODEL_LOGS_DIR_NAME, str(i) +'_steps_SpeechRecognitionModelV1.model'))
    m.ctc_model.save_weights(os.path.join(MODEL_LOGS_DIR_NAME, str(i) +'_steps_SpeechRecognitionModelV1.model.base'))



Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
Model: "model_2"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
the_inputs (InputLayer)         (None, None, 200, 1) 0                                            
__________________________________________________________________________________________________
conv2d_1 (Conv2D)               (None, None, 200, 32 288         the_inputs[0][0]                 
__________________________________________________________________________________________________
batch_normalization_1 (BatchNor (None, None, 200, 32 128         conv2d_1[0][0]                   
__________________________________________________________________________________________________
conv2d_2 (Conv2D)               (None, None, 200, 32 9248        batch_normalization_1[0][0]    

dense_3 (Dense)                 (None, None, 1424)   183696      batch_normalization_16[0][0]     
__________________________________________________________________________________________________
y_pred_activation (Activation)  (None, None, 1424)   0           dense_3[0][0]                    
__________________________________________________________________________________________________
the_labels (InputLayer)         (None, None)         0                                            
__________________________________________________________________________________________________
input_length (InputLayer)       (None, 1)            0                                            
__________________________________________________________________________________________________
label_length (InputLayer)       (None, 1)            0                                            
__________________________________________________________________________________________________
ctc_loss (

  185/20000 [..............................] - ETA: 32:17:19 - loss: 64.9330 - acc: 0.0000e+ - ETA: 18:44:54 - loss: 67.0409 - acc: 0.0000e+ - ETA: 14:34:19 - loss: 74.6383 - acc: 0.0000e+ - ETA: 12:19:01 - loss: 65.6995 - acc: 0.0000e+ - ETA: 10:48:33 - loss: 68.2564 - acc: 0.0000e+ - ETA: 9:58:43 - loss: 66.5344 - acc: 0.0000e+00 - ETA: 8:40:13 - loss: 65.1714 - acc: 0.0000e+0 - ETA: 8:17:02 - loss: 65.0063 - acc: 0.0312    - ETA: 7:28:52 - loss: 68.5876 - acc: 0.027 - ETA: 7:07:22 - loss: 70.2712 - acc: 0.025 - ETA: 7:13:45 - loss: 69.6515 - acc: 0.045 - ETA: 7:00:44 - loss: 70.5741 - acc: 0.041 - ETA: 6:52:10 - loss: 72.5445 - acc: 0.038 - ETA: 6:42:50 - loss: 71.4575 - acc: 0.035 - ETA: 6:40:31 - loss: 72.4559 - acc: 0.033 - ETA: 6:33:18 - loss: 71.4003 - acc: 0.031 - ETA: 6:30:32 - loss: 73.0483 - acc: 0.029 - ETA: 6:26:45 - loss: 72.5136 - acc: 0.041 - ETA: 6:27:30 - loss: 71.3445 - acc: 0.052 - ETA: 6:18:43 - loss: 70.4320 - acc: 0.050 - ETA: 6:14:57 - loss: 69.5360 - acc: 0.04

  371/20000 [..............................] - ETA: 3:18:44 - loss: 61.4972 - acc: 0.014 - ETA: 3:18:08 - loss: 61.5445 - acc: 0.014 - ETA: 3:17:17 - loss: 61.4951 - acc: 0.014 - ETA: 3:16:39 - loss: 61.5880 - acc: 0.014 - ETA: 3:15:49 - loss: 61.4481 - acc: 0.014 - ETA: 3:15:01 - loss: 61.3239 - acc: 0.014 - ETA: 3:14:12 - loss: 61.1147 - acc: 0.014 - ETA: 3:14:44 - loss: 61.1789 - acc: 0.014 - ETA: 3:14:00 - loss: 61.1440 - acc: 0.014 - ETA: 3:13:17 - loss: 61.0803 - acc: 0.014 - ETA: 3:12:28 - loss: 60.9255 - acc: 0.014 - ETA: 3:12:47 - loss: 60.9815 - acc: 0.014 - ETA: 3:12:00 - loss: 60.9774 - acc: 0.013 - ETA: 3:11:14 - loss: 60.9807 - acc: 0.013 - ETA: 3:10:36 - loss: 60.9558 - acc: 0.013 - ETA: 3:10:08 - loss: 60.8402 - acc: 0.013 - ETA: 3:10:47 - loss: 60.6378 - acc: 0.013 - ETA: 3:10:30 - loss: 60.5422 - acc: 0.013 - ETA: 3:09:45 - loss: 60.4382 - acc: 0.013 - ETA: 3:09:23 - loss: 60.3505 - acc: 0.013 - ETA: 3:09:58 - loss: 60.2557 - acc: 0.013 - ETA: 3:09:35 - loss: 60.1396 

  557/20000 [..............................] - ETA: 2:24:29 - loss: 54.5866 - acc: 0.012 - ETA: 2:25:13 - loss: 54.5695 - acc: 0.012 - ETA: 2:24:59 - loss: 54.5616 - acc: 0.012 - ETA: 2:24:48 - loss: 54.5463 - acc: 0.012 - ETA: 2:24:32 - loss: 54.5396 - acc: 0.012 - ETA: 2:24:16 - loss: 54.4748 - acc: 0.011 - ETA: 2:24:00 - loss: 54.4251 - acc: 0.011 - ETA: 2:23:44 - loss: 54.3361 - acc: 0.011 - ETA: 2:23:42 - loss: 54.2920 - acc: 0.011 - ETA: 2:23:42 - loss: 54.2058 - acc: 0.011 - ETA: 2:23:29 - loss: 54.2043 - acc: 0.011 - ETA: 2:23:17 - loss: 54.1740 - acc: 0.011 - ETA: 2:23:14 - loss: 54.1162 - acc: 0.011 - ETA: 2:23:15 - loss: 54.0156 - acc: 0.011 - ETA: 2:23:03 - loss: 53.9933 - acc: 0.011 - ETA: 2:22:48 - loss: 53.9755 - acc: 0.011 - ETA: 2:22:33 - loss: 53.9379 - acc: 0.011 - ETA: 2:22:19 - loss: 53.9704 - acc: 0.011 - ETA: 2:22:06 - loss: 53.9378 - acc: 0.011 - ETA: 2:21:51 - loss: 53.9821 - acc: 0.011 - ETA: 2:21:38 - loss: 54.0190 - acc: 0.011 - ETA: 2:21:26 - loss: 54.0439 

...

 7992/20000 [==========>...................] - ETA: 43:54 - loss: 4.9559 - acc: 0.15 - ETA: 43:54 - loss: 4.9559 - acc: 0.15 - ETA: 43:54 - loss: 4.9559 - acc: 0.15 - ETA: 43:54 - loss: 4.9559 - acc: 0.15 - ETA: 43:54 - loss: 4.9560 - acc: 0.15 - ETA: 43:53 - loss: 4.9558 - acc: 0.15 - ETA: 43:53 - loss: 4.9564 - acc: 0.15 - ETA: 43:53 - loss: 4.9566 - acc: 0.15 - ETA: 43:53 - loss: 4.9570 - acc: 0.15 - ETA: 43:53 - loss: 4.9571 - acc: 0.15 - ETA: 43:52 - loss: 4.9567 - acc: 0.15 - ETA: 43:52 - loss: 4.9568 - acc: 0.15 - ETA: 43:52 - loss: 4.9568 - acc: 0.15 - ETA: 43:52 - loss: 4.9567 - acc: 0.15 - ETA: 43:51 - loss: 4.9570 - acc: 0.15 - ETA: 43:51 - loss: 4.9580 - acc: 0.15 - ETA: 43:51 - loss: 4.9579 - acc: 0.15 - ETA: 43:50 - loss: 4.9582 - acc: 0.15 - ETA: 43:50 - loss: 4.9579 - acc: 0.15 - ETA: 43:50 - loss: 4.9577 - acc: 0.15 - ETA: 43:50 - loss: 4.9585 - acc: 0.15 - ETA: 43:49 - loss: 4.9588 - acc: 0.15 - ETA: 43:49 - loss: 4.9586 - acc: 0.15 - ETA: 43:49 - loss: 4.9589 - acc: 

 8196/20000 [===========>..................] - ETA: 43:06 - loss: 4.9557 - acc: 0.15 - ETA: 43:05 - loss: 4.9561 - acc: 0.15 - ETA: 43:05 - loss: 4.9560 - acc: 0.15 - ETA: 43:05 - loss: 4.9560 - acc: 0.15 - ETA: 43:05 - loss: 4.9559 - acc: 0.15 - ETA: 43:04 - loss: 4.9559 - acc: 0.15 - ETA: 43:04 - loss: 4.9554 - acc: 0.15 - ETA: 43:04 - loss: 4.9563 - acc: 0.15 - ETA: 43:04 - loss: 4.9563 - acc: 0.15 - ETA: 43:04 - loss: 4.9558 - acc: 0.15 - ETA: 43:04 - loss: 4.9559 - acc: 0.15 - ETA: 43:03 - loss: 4.9557 - acc: 0.15 - ETA: 43:03 - loss: 4.9555 - acc: 0.15 - ETA: 43:03 - loss: 4.9554 - acc: 0.15 - ETA: 43:03 - loss: 4.9552 - acc: 0.15 - ETA: 43:03 - loss: 4.9553 - acc: 0.15 - ETA: 43:02 - loss: 4.9554 - acc: 0.15 - ETA: 43:02 - loss: 4.9551 - acc: 0.15 - ETA: 43:02 - loss: 4.9549 - acc: 0.15 - ETA: 43:02 - loss: 4.9550 - acc: 0.15 - ETA: 43:02 - loss: 4.9550 - acc: 0.15 - ETA: 43:01 - loss: 4.9548 - acc: 0.15 - ETA: 43:01 - loss: 4.9546 - acc: 0.15 - ETA: 43:01 - loss: 4.9541 - acc: 

 8400/20000 [===========>..................] - ETA: 42:26 - loss: 4.9596 - acc: 0.15 - ETA: 42:26 - loss: 4.9597 - acc: 0.15 - ETA: 42:25 - loss: 4.9593 - acc: 0.15 - ETA: 42:25 - loss: 4.9591 - acc: 0.15 - ETA: 42:25 - loss: 4.9588 - acc: 0.15 - ETA: 42:24 - loss: 4.9587 - acc: 0.15 - ETA: 42:24 - loss: 4.9585 - acc: 0.15 - ETA: 42:24 - loss: 4.9586 - acc: 0.15 - ETA: 42:24 - loss: 4.9586 - acc: 0.15 - ETA: 42:23 - loss: 4.9598 - acc: 0.15 - ETA: 42:23 - loss: 4.9598 - acc: 0.15 - ETA: 42:23 - loss: 4.9596 - acc: 0.15 - ETA: 42:23 - loss: 4.9605 - acc: 0.15 - ETA: 42:23 - loss: 4.9603 - acc: 0.15 - ETA: 42:23 - loss: 4.9604 - acc: 0.15 - ETA: 42:23 - loss: 4.9609 - acc: 0.15 - ETA: 42:22 - loss: 4.9605 - acc: 0.15 - ETA: 42:22 - loss: 4.9611 - acc: 0.15 - ETA: 42:22 - loss: 4.9605 - acc: 0.15 - ETA: 42:21 - loss: 4.9602 - acc: 0.15 - ETA: 42:21 - loss: 4.9601 - acc: 0.15 - ETA: 42:21 - loss: 4.9601 - acc: 0.15 - ETA: 42:21 - loss: 4.9608 - acc: 0.15 - ETA: 42:21 - loss: 4.9606 - acc: 

 8604/20000 [===========>..................] - ETA: 41:44 - loss: 4.9665 - acc: 0.15 - ETA: 41:44 - loss: 4.9669 - acc: 0.15 - ETA: 41:44 - loss: 4.9669 - acc: 0.15 - ETA: 41:44 - loss: 4.9667 - acc: 0.15 - ETA: 41:43 - loss: 4.9664 - acc: 0.15 - ETA: 41:43 - loss: 4.9668 - acc: 0.15 - ETA: 41:43 - loss: 4.9669 - acc: 0.15 - ETA: 41:43 - loss: 4.9669 - acc: 0.15 - ETA: 41:42 - loss: 4.9669 - acc: 0.15 - ETA: 41:42 - loss: 4.9673 - acc: 0.15 - ETA: 41:42 - loss: 4.9674 - acc: 0.15 - ETA: 41:42 - loss: 4.9678 - acc: 0.15 - ETA: 41:42 - loss: 4.9683 - acc: 0.15 - ETA: 41:42 - loss: 4.9683 - acc: 0.15 - ETA: 41:42 - loss: 4.9686 - acc: 0.15 - ETA: 41:42 - loss: 4.9682 - acc: 0.15 - ETA: 41:41 - loss: 4.9679 - acc: 0.15 - ETA: 41:41 - loss: 4.9677 - acc: 0.15 - ETA: 41:41 - loss: 4.9673 - acc: 0.15 - ETA: 41:41 - loss: 4.9672 - acc: 0.15 - ETA: 41:40 - loss: 4.9677 - acc: 0.15 - ETA: 41:40 - loss: 4.9678 - acc: 0.15 - ETA: 41:40 - loss: 4.9674 - acc: 0.15 - ETA: 41:40 - loss: 4.9675 - acc: 

 8691/20000 [============>.................] - ETA: 41:03 - loss: 4.9710 - acc: 0.15 - ETA: 41:03 - loss: 4.9706 - acc: 0.15 - ETA: 41:03 - loss: 4.9706 - acc: 0.15 - ETA: 41:02 - loss: 4.9708 - acc: 0.15 - ETA: 41:02 - loss: 4.9707 - acc: 0.15 - ETA: 41:02 - loss: 4.9708 - acc: 0.15 - ETA: 41:02 - loss: 4.9707 - acc: 0.15 - ETA: 41:02 - loss: 4.9704 - acc: 0.15 - ETA: 41:01 - loss: 4.9700 - acc: 0.15 - ETA: 41:01 - loss: 4.9697 - acc: 0.15 - ETA: 41:01 - loss: 4.9706 - acc: 0.15 - ETA: 41:00 - loss: 4.9707 - acc: 0.15 - ETA: 41:00 - loss: 4.9710 - acc: 0.15 - ETA: 41:00 - loss: 4.9714 - acc: 0.15 - ETA: 41:00 - loss: 4.9719 - acc: 0.15 - ETA: 41:00 - loss: 4.9716 - acc: 0.15 - ETA: 40:59 - loss: 4.9711 - acc: 0.15 - ETA: 40:59 - loss: 4.9715 - acc: 0.15 - ETA: 40:59 - loss: 4.9711 - acc: 0.15 - ETA: 40:59 - loss: 4.9712 - acc: 0.15 - ETA: 40:58 - loss: 4.9712 - acc: 0.15 - ETA: 40:58 - loss: 4.9708 - acc: 0.15 - ETA: 40:58 - loss: 4.9705 - acc: 0.15 - ETA: 40:58 - loss: 4.9705 - acc: 